<a href="https://colab.research.google.com/github/Xiar-fatah/Stock-Market-Patterns/blob/ADD_PCA/FORD_STOCK_MODEL_ONE_FEATURE_remember.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
! git clone https://github.com/Xiar-fatah/Stock-Market-Patterns

Cloning into 'Stock-Market-Patterns'...
remote: Enumerating objects: 113, done.
remote: Counting objects: 100% (113/113), done.
remote: Compressing objects: 100% (84/84), done.
remote: Total 391 (delta 44), reused 81 (delta 26), pack-reused 278
Receiving objects: 100% (391/391), 3.11 MiB | 6.08 MiB/s, done.
Resolving deltas: 100% (186/186), done.


In [0]:
# Importing necessary tools for machine learning
import torch
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from sklearn.preprocessing import MinMaxScaler
import plotly.graph_objects as go


In [0]:
# Importing data.py and ERRORS.py
import sys
sys.path.append('/content/Stock-Market-Patterns/Core')
import data
import ERRORS

In [0]:
class LSTM(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, output_size,batch_size):
        super(LSTM, self).__init__()
        self.input_size = input_size
        self.hidden_size = hidden_size 
        self.num_layers = num_layers 
        self.output_size = output_size 
        self.batch_size = batch_size 
        self.hidden_state = self.hidden_cell()
        self.lstm = nn.LSTM(self.input_size, self.hidden_size, self.num_layers, dropout = 0.5)
        self.linear = nn.Linear(hidden_size, output_size)
        
    def hidden_cell(self):
        h_0,c_0 = (torch.zeros(self.num_layers, self.batch_size, self.hidden_size), 
        torch.zeros(self.num_layers, self.batch_size, self.hidden_size))
        return h_0,c_0 
    
    def forward(self, t):
        t = t.reshape(20,1,1)
        t, self.hidden_state = self.lstm(t, (self.hidden_state))
        t = self.linear(self.hidden_state[0][-1].detach())
        return t[0]

In [0]:
model = LSTM(input_size = 1, hidden_size = 128,
                num_layers = 2, output_size = 1, batch_size = 1)
learning_rate = 0.001
loss_function = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
epochs = 1000
# For plot title
hidden_size = 128
num_layers = 2


In [0]:
train = data.trainloader
test = data.testloader

for epoch in range(epochs):
    for i, (seq, labels) in enumerate(train):
        optimizer.zero_grad()
        output = model(seq)
        loss = loss_function(output, labels)
        loss.backward()
        optimizer.step()
        
    if (epoch + 1) % 10 == 0:
            print("Epoch: {}, Loss: {:.5f}".format(epoch + 1, loss.item()))

    #Evaluation
    model.eval()
    predictions = []
    with torch.no_grad():
        for i, (seq, labels) in enumerate(test):
            output = model(seq)
            predictions.append(output.tolist()[0])
    predictions = np.add(np.multiply(predictions,data.std),data.mean)
    real = data.real
    print("RMS: " + str(ERRORS.RMS(predictions, real)) + "\n"
        "MAPE: " + str(ERRORS.MAPE(predictions, real)) + "\n"
        "MAE: " + str(ERRORS.MAE(predictions, real)) + "\n"
        "R: " + str(ERRORS.R(predictions, real)))    



    x = np.linspace(0,999,1000)

    fig = go.Figure()
    fig.add_trace(go.Scatter(
                    x = x,
                    y = real,
                    name="Closing price for FORD",
                    line_color='deepskyblue',
                    opacity=0.8))

    fig.add_trace(go.Scatter(
                    x = x,
                    y = predictions,
                    name="Predictions",
                    line_color='dimgray',
                    opacity=0.8))
    fig.update_layout(title_text='Plot for learning rate: ' + str(learning_rate) + ' , epoch: ' + str(epoch + 1) + ' hidden_size: ' + str(hidden_size) + ' and num_layers: ' + str(num_layers),
                      xaxis_rangeslider_visible=True,
                      xaxis_title='Time',
                      yaxis_title='US Dollars')

    fig.show()

RMS: 67.3621177412583
MAPE: 0.1323900816085061
MAE: 1.2775600817196577
R: 0.999748485029694


RMS: 2.409158114893241
MAPE: 0.020450856552736752
MAE: 0.20514984105960238
R: 0.999748720563054


RMS: 2.733528355304474
MAPE: 0.021648421443562983
MAE: 0.2248815291717919
R: 0.9997500741534844


RMS: 1.9023716281536345
MAPE: 0.017346101240975322
MAE: 0.18001054787630763
R: 0.9997518558288306


RMS: 1.855469197936542
MAPE: 0.017197122692979676
MAE: 0.17801900841069734
R: 0.999753681237398


...

RMS: 1.4558223584761139
MAPE: 0.015098502481379669
MAE: 0.15501121788034855
R: 0.9998823060388953


RMS: 1.3160248394764869
MAPE: 0.01415194060038291
MAE: 0.1468287014120976
R: 0.9998831374790451


RMS: 6.665679630241974
MAPE: 0.03969531577758063
MAE: 0.42563904062257507
R: 0.9998850549274493


RMS: 1.3650679229563494
MAPE: 0.014592393544206057
MAE: 0.14998242710253473
R: 0.99988536896211


KeyboardInterrupt: ignored